In [1]:
from rank_bm25 import BM25Okapi
import chromadb
import spacy

In [2]:
chromadb_path = './chromadb'
collection_name = 'cera'
chroma_client = chromadb.PersistentClient(path=chromadb_path)
collection = chroma_client.get_collection(name=collection_name)

In [3]:
collection.get().keys()

dict_keys(['ids', 'embeddings', 'metadatas', 'documents', 'uris', 'data'])

In [4]:
docs = collection.get()['documents']

In [5]:
ids = collection.get()['ids']

In [6]:
len(docs)

2896

In [7]:
docs_tokenized = [doc.replace("\n", " ").split(" ") for doc in docs]

In [8]:
docs_tokenized[0]

['Le',
 'paiement',
 'sans',
 'contact',
 '',
 'Les',
 'points',
 'clés',
 '',
 'Pratique',
 'Plus',
 'besoin',
 'de',
 'chercher',
 'de',
 'la',
 'monnaie',
 'pour',
 'régler',
 'votre',
 'café,',
 'parking,',
 'repas,',
 'journal…',
 'Gratuit',
 'Cette',
 'fonctionnalité',
 'est',
 'ajoutée',
 'automatiquement',
 'et',
 'gratuitement',
 'à',
 'votre',
 'carte.',
 'Rapide',
 'Vous',
 'réglez',
 'votre',
 'achat',
 'd’un',
 'simple',
 'geste,',
 'sans',
 'insérer',
 'votre',
 'carte',
 'ni',
 'composer',
 'votre',
 'code',
 'confidentiel.']

In [9]:
nlp = spacy.load('fr_core_news_md')

In [29]:
for tok in nlp(docs[0]):
    print(tok, tok.lemma_, tok.pos_, tok.ent_iob_, tok.ent_type_)

Le le DET O 
paiement paiement NOUN O 
sans sans ADP O 
contact contact NOUN O 


 

 SPACE O 
Les le DET O 
points point NOUN O 
clés clé ADJ O 


 

 SPACE O 
Pratique pratique NOUN B MISC
Plus plus ADV I MISC
besoin besoin NOUN O 
de de ADP O 
chercher chercher VERB O 
de de ADP O 
la le DET O 
monnaie monnaie NOUN O 
pour pour ADP O 
régler régler VERB O 
votre votre DET O 
café café NOUN O 
, , PUNCT O 
parking parking NOUN O 
, , PUNCT O 
repas repas NOUN O 
, , PUNCT O 
journal journal NOUN O 
… … PUNCT O 

 
 SPACE O 
Gratuit gratuit NOUN B MISC
Cette ce DET O 
fonctionnalité fonctionnalité NOUN O 
est être AUX O 
ajoutée ajouter VERB O 
automatiquement automatiquement ADV O 
et et CCONJ O 
gratuitement gratuitement NOUN O 
à à ADP O 
votre votre DET O 
carte carte NOUN O 
. . PUNCT O 

 
 SPACE O 
Rapide rapide NOUN B MISC
Vous vous PRON I MISC
réglez régler VERB I MISC
votre votre DET I MISC
achat achat NOUN I MISC
d’ d’ ADP I MISC
un un DET I MISC
simple simple ADJ I MISC
ge

In [32]:
def keep_token(tok):
    return tok.pos_ == 'NOUN' or tok.pos_ == 'VERB' or \
           tok.pos_ == 'PROPN' or tok.pos_ == 'ADJ'

In [33]:
def lemmatize(str):
    res = []
    for tok in nlp(str):
        if keep_token(tok):
            res.append(tok.lemma_)
    return res

In [34]:
docs_tokenized = []
for doc in docs:
    toks = lemmatize(doc)
    if len(toks)>0: docs_tokenized.append(toks)

In [35]:
bm25_db = BM25Okapi(docs_tokenized)

In [36]:
query = "Comment procéder pour déclarer un sinistre Visa Premier ?"

In [37]:
query_toks = lemmatize(query)

In [38]:
query_toks

['procéder', 'déclarer', 'sinistre', 'Visa', 'premier']

In [39]:
# query_tokenized = query.split(" ")
doc_scores = bm25_db.get_scores(query_toks)

In [40]:
len(doc_scores)

2896

In [41]:
ids_scores = dict(zip(ids, doc_scores))

In [42]:
sorted_ids_scores = sorted(ids_scores.items(), key=lambda x: x[1], reverse=True)

In [43]:
dict(sorted_ids_scores[:3])

{'d42d7174ce.html-1': 18.401661345931544,
 'c98558432b.html-2': 16.991284762126078,
 'd42d7174ce.html-2': 13.443119955565379}

In [57]:
def size_query_inter_doc(query_str, doc_id):
    query_toks = lemmatize(query_str)
    doc_toks = lemmatize(collection.get(ids=[doc_id])['documents'][0])
    return len(set(query_toks) & set(doc_toks))

In [59]:
size_query_inter_doc(query, 'd42d7174ce.html-1')

3

In [54]:
set(query_toks) & set(lemmatize(collection.get(ids=['c98558432b.html-2'])['documents'][0]))

{'Visa', 'déclarer', 'premier', 'sinistre'}

In [55]:
set(query_toks) & set(lemmatize(collection.get(ids=['d42d7174ce.html-1'])['documents'][0]))

{'déclarer', 'procéder', 'sinistre'}

In [56]:
set(query_toks) & set(lemmatize(collection.get(ids=['d42d7174ce.html-2'])['documents'][0]))

{'déclarer', 'sinistre'}

In [47]:
collection.get(ids=list(dict(sorted_ids_scores[:3]).keys()))

{'ids': ['c98558432b.html-2', 'd42d7174ce.html-1', 'd42d7174ce.html-2'],
 'embeddings': None,
 'metadatas': [{'category': 'comptes-cartes',
   'url': 'https://www.caisse-epargne.fr/rhone-alpes/comptes-cartes/garanties-assurances-et-assistances-des-cartes-visa/'},
  {'category': 'assurer',
   'url': 'https://www.caisse-epargne.fr/rhone-alpes/assurer/declaration-sinistre-intemperies/'},
  {'category': 'assurer',
   'url': 'https://www.caisse-epargne.fr/rhone-alpes/assurer/declaration-sinistre-intemperies/'}],
 'documents': ['Garanties Assurances et Assistance des cartes Visa\n\nGaranties Assurances et Assistance des cartes Visa\n\n• La déclaration de sinistre doit être faite dans les 15 jours suivant la date à laquelle a eu lieu le sinistre ;\n\n• Les indemnisations interviennent a posteriori du sinistre sur présentation de justificatifs.\nLe porteur de la Carte Visa, ainsi que son conjoint ou concubin vivant sous le même toit et ses enfants célibataires de moins de 25 ans fiscalement à 

In [70]:
'\n\n'.join((collection.get(ids=['c98558432b.html-2'])['documents'][0]).split('\n\n')[2:])

'• La déclaration de sinistre doit être faite dans les 15 jours suivant la date à laquelle a eu lieu le sinistre ;\n\n• Les indemnisations interviennent a posteriori du sinistre sur présentation de justificatifs.\nLe porteur de la Carte Visa, ainsi que son conjoint ou concubin vivant sous le même toit et ses enfants célibataires de moins de 25 ans fiscalement à sa charge, même s’ils voyagent séparément.\n• Tout déplacement ou séjour à une distance supérieure à 100 km de la résidence principale de l’Assuré ou de son lieu de travail habituel, dans la limite des 180 premiers jours consécutifs ;\n\n• Sans franchise kilométrique pour la Garantie Neige et Montagne.\nPour déclarer un sinistre, vous devez vous rendre sur le site :\nLes garanties d’assistance sont valables toute la durée du séjour/déplacement dans la limite de 90 jours.\nLe porteur de la Carte Visa, ainsi que son conjoint ou concubin vivant sous le même toit et ses enfants célibataires de moins de 25 ans fiscalement à sa charge

In [35]:
nb_passage = 1
while True:
    id = "25dcc77e00.html-" + str(nb_passage)
    passages = collection.get(ids=[id])
    if len(passages['documents']) > 0:
        print(passages['documents'][0])
        print("\n----------\n")
        nb_passage += 1
    else:
        break

Carte Visa Premier

Les points clés

Innovation Paiement sans contact(1) et paiement mobile compatible(2).
Garanties d’Assurances et Assistance(3) Vous vous protégez ainsi que votre famille lors de vos déplacements en France et à l’étranger.
Plafonds élevés Bénéficiez de souplesse grâce à des plafonds de paiement et retraits supérieurs à ceux d’une Visa Classic.

----------

Carte Visa Premier

Carte Visa Premier, toujours à vos côtés

Carte de paiement et de retrait utilisable en France et à l’étranger ;
Des plafonds de paiement et de retrait élevés ;
Des Garanties d’Assurances et d’Assistance incluses pour vous protéger, vous et votre famille, lors de vos déplacements en France et à l’étranger (une couverture assurances et assistance médicale dès que vous être à plus de 100kms de votre domicile);– Exemples de garanties :En voyage : modification ou annulation de voyage, responsabilité civile, rapatriement en cas de maladie ou d’accident, remboursement des frais médicaux à l’étranger, 

In [52]:
query = "Quel est le risque de perte en capital pour un sociétaire ?"
query_tokenized = query.split(" ")
doc_scores = bm25_db.get_scores(query_tokenized)
ids_scores = dict(zip(ids, doc_scores))
sorted_ids_scores = sorted(ids_scores.items(), key=lambda x: x[1], reverse=True)

In [53]:
sorted_ids_scores[:10]

[('f6d921ced8.html-3', 29.446670121305353),
 ('ff83960e9d.html-1', 24.88880087849239),
 ('ecb10d12cf.html-2', 24.206423694569803),
 ('f753c94bb4.html-1', 24.009169917059968),
 ('dbdc338e94.html-7', 23.845667609823003),
 ('f66629c8b6.html-2', 23.779561367699497),
 ('9b9d084514.html-2', 23.770317569985096),
 ('6123ccc4f8.html-6', 23.732579312988157),
 ('c145d2aa96.html-4', 23.48215739435705),
 ('286a391488.html-2', 23.443469979811134)]

In [51]:
collection.get(ids=['f6d921ced8.html-3'])

{'ids': ['f6d921ced8.html-3'],
 'embeddings': None,
 'metadatas': [{'category': 'votre-banque',
   'url': 'https://www.caisse-epargne.fr/rhone-alpes/votre-banque/nos-engagements/etre-societaire/'}],
 'documents': ['Devenez sociétaire !\n\nQui peut devenir sociétaire ?\n\nSi vous souhaitez que la SLE rachète vos parts sociales, votre demande, soumise à l’autorisation du conseil d’administration de la SLE, doit être formulée avant le 31 mai, date de clôture de l’exercice. De ce fait, aucune assurance ne peut être donnée quant à la liquidité des parts sociales.\n\nPar ailleurs, les rachats de parts sociales sont subordonnés au respect du capital minimum en deçà duquel la SLE ne peut descendre. En conséquence, les sociétaires doivent être conscients qu’ils pourraient ne pas être en mesure de céder facilement leurs parts sociales.\n\nLe remboursement effectif, qu’il soit consécutif à la perte de la qualité de sociétaire ou à une demande de rachat, intervient le 1er jour ouvré du nouvel exer